# IMDB-WIKI Knowledge Graph

In [110]:
import os
import os.path as osp
from os.path import join
from glob import glob
import random
import math
from datetime import datetime
import requests
import json
import urllib

import cv2 as cv
import pandas as pd
from scipy.io import loadmat
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt

from tqdm import tqdm_notebook as tqdm
%reload_ext autoreload
%autoreload 2

## Load Metadata

In [5]:
fp_meta = '/data_store_hdd/datasets/people/imdb_wiki/metadata/imdb_wiki.csv'

In [6]:
df_meta = pd.read_csv(fp_meta).set_index('index')

In [7]:
df_meta.head()

celeb_id        dob                                      filepath  \
index                                                                      
0          6488  1900-5-11   01/nm0000001_rm124825600_1899-5-10_1968.jpg   
1          6488  1900-5-11  01/nm0000001_rm3343756032_1899-5-10_1970.jpg   
2          6488  1900-5-11   01/nm0000001_rm577153792_1899-5-10_1968.jpg   
3          6488  1900-5-11   01/nm0000001_rm946909184_1899-5-10_1968.jpg   
4          6488  1900-5-11   01/nm0000001_rm980463616_1899-5-10_1968.jpg   

      gender          name           x1           x2          y1          y2  \
index                                                                          
0          m  Fred Astaire  1072.926000  1214.784000  161.838000  303.696000   
1          m  Fred Astaire   477.184000   622.592000  100.352000  245.760000   
2          m  Fred Astaire   114.969643   451.686572  114.969643  451.686572   
3          m  Fred Astaire   622.885506   844.339008  424.217504  645.671006   
4          m  Fred Astaire  1013.859002  1201.586128  233.882042  421.609168   

       year_photo  
index              
0            1968  
1            1970  
2            1968  
3            1968  
4            1968

In [ ]:
ids

In [8]:
api_key = open('/work/megapixels_dev/3rdparty/knowledge-graph-api/.api_key').read()

def get_knowledge(q, api_key):
  service_url = 'https://kgsearch.googleapis.com/v1/entities:search'
  params = {
      'query': q,
      'limit': 5,
      'indent': True,
      'key': api_key,
      }
  url = service_url + '?' + urllib.parse.urlencode(params)  # TODO: use requests
  response = json.loads(urllib.request.urlopen(url).read())
  response = response.get('itemListElement', [])
  if len(response) > 0:
    result = response[0].get('result', [])
    result['score'] = response[0]['resultScore']
    return result
  else:
    return []

In [106]:
# test
q = 'Xi Jinping'
r = get_knowledge(q, api_key)
print(r['description'])
print(r['name'])
print(r['url'])
print(r['score'])

General Secretary of the Communist Party of China
Xi Jinping


KeyError: 'url'

In [107]:
from pprint import pprint

In [108]:
print(r['@id'])

kg:/m/06ff60


In [89]:
pprint(r)

{'@id': 'kg:/g/11f4ksbzcm',
 '@type': ['Thing', 'Event'],
 'detailedDescription': {'articleBody': 'On February 14, 2018, a gunman opened '
                                        'fire at Marjory Stoneman Douglas High '
                                        'School in Parkland, Florida, killing '
                                        'seventeen students and staff members '
                                        'and injuring seventeen others. ',
                         'license': 'https://en.wikipedia.org/wiki/Wikipedia:Text_of_Creative_Commons_Attribution-ShareAlike_3.0_Unported_License',
                         'url': 'https://en.wikipedia.org/wiki/Stoneman_Douglas_High_School_shooting'},
 'image': {'contentUrl': 'http://t1.gstatic.com/images?q=tbn:ANd9GcQmY7VqmGt4zEJU8Rc4EwPWroYd-L0QQ5wkZfiFO-WRqNBC-FPN',
           'url': 'https://en.wikipedia.org/wiki/Stoneman_Douglas_High_School_shooting'},
 'name': 'Stoneman Douglas High School shooting',
 'score': 60.411652}


In [20]:
dir_msceleb = '/data_store_hdd/datasets/people/msceleb/media/original/'

In [64]:
kgs_msceleb = os.listdir(dir_msceleb)
kgs_msceleb = ['/' + x.replace('.','/') for x in kgs_msceleb]

In [109]:
'/m/06ff60' in kgs_msceleb

True

In [111]:
def get_kg_by_id(kg_id, api_key):
  service_url = 'https://kgsearch.googleapis.com/v1/entities:search'
  params = {
      'ids': kg_id,
      'limit': 1,
      'indent': True,
      'key': api_key,
      }
  url = service_url + '?' + urllib.parse.urlencode(params)  # TODO: use requests
  try:
    response = json.loads(urllib.request.urlopen(url).read())
    response = response.get('itemListElement', [])
    result = response[0].get('result', [])
    result['score'] = response[0]['resultScore']
    return result
  except Exception as e:
    return []

In [122]:
a = get_kg_by_id('/m/0100n5bs', api_key)

In [123]:
a

[]